In [213]:
!scrapy startproject cartrider

Error: scrapy.cfg already exists in /home/ubuntu/python3/notebook/crawling_project/cartrider


In [239]:
%%writefile cartrider/cartrider/items.py
import scrapy

class CartriderItem(scrapy.Item):
    matches = scrapy.Field()
    trackId = scrapy.Field()
    kart = scrapy.Field()
    matchRank = scrapy.Field()
    rankinggrade2 = scrapy.Field()

Overwriting cartrider/cartrider/items.py


In [1]:
%%writefile cartrider/cartrider/spiders/spider.py

import scrapy
import pandas as pd
import numpy as np
import json
import requests
from cartrider.items import CartriderItem

class CartriderSpider(scrapy.Spider):
    name = "Cartrider"
    headers = {
        "Content-Type": "application/json; charset=utf-8",
        "Authorization": "api_key",
    }
    
    def start_requests(self):
        dates = list(zip(pd.date_range("2019-06-01","2019-12-02").strftime("%Y%m%d"), pd.date_range("2019-06-02","2019-12-03").strftime("%Y%m%d")))
        match_type = "7b9f0fd5377c38514dbb78ebe63ac6c3b81009d5a31dd569d1cff8f005aa881a" # spped indi
        url_format = "https://api.nexon.co.kr/kart/v1.0/matches/all?start_date={start_date}&end_date={end_date}&offset={offset}&limit=200&match_types={match_types}"
        for start_date, end_date in dates:
            for i in list(np.linspace(0,1000,6)):
                url = url_format.format(start_date=start_date, end_date=end_date, offset=0, limit=200, match_types=match_type)
                yield scrapy.http.Request(url, headers=self.headers, callback=self.parse)
        
    def parse(self, response):
        matches = json.loads(response.body)["matches"][0]["matches"]
        for match in matches:
            url_m = "https://api.nexon.co.kr/kart/v1.0/matches/{match_id}".format(match_id=match)
            resp = requests.get(url_m, headers=self.headers)
            data1 = resp.json()["players"]
            if len(data1) == 8:
                yield scrapy.http.Request(url_m, headers=self.headers, callback=self.match_parse)
            else:
                continue
            
    def match_parse(self, response):
        item = CartriderItem()
        for i in range(0,8):
            item["matches"] = json.loads(response.body)["matchId"]
            item["trackId"] = json.loads(response.body)["trackId"]
            item["kart"] = json.loads(response.body)["players"][i]["kart"]
            item["matchRank"] = json.loads(response.body)["players"][i]["matchRank"]
            item["rankinggrade2"] = json.loads(response.body)["players"][i]["rankinggrade2"]
            yield item

Overwriting cartrider/cartrider/spiders/spider.py


In [266]:
%%writefile run.sh
cd cartrider
scrapy crawl Cartrider -o kart.csv

Overwriting run.sh


In [267]:
!chmod +x run.sh

In [2]:
!./run.sh

2019-12-05 15:32:48 [scrapy.utils.log] INFO: Scrapy 1.8.0 started (bot: cartrider)
2019-12-05 15:32:48 [scrapy.utils.log] INFO: Versions: lxml 4.4.2.0, libxml2 2.9.9, cssselect 1.1.0, parsel 1.5.2, w3lib 1.21.0, Twisted 19.10.0, Python 3.6.9 (default, Oct 24 2019, 05:23:48) - [GCC 7.4.0], pyOpenSSL 19.1.0 (OpenSSL 1.1.1d  10 Sep 2019), cryptography 2.8, Platform Linux-4.15.0-1056-aws-x86_64-with-debian-buster-sid
2019-12-05 15:32:48 [scrapy.crawler] INFO: Overridden settings: {'BOT_NAME': 'cartrider', 'FEED_FORMAT': 'csv', 'FEED_URI': 'cart.csv', 'NEWSPIDER_MODULE': 'cartrider.spiders', 'ROBOTSTXT_OBEY': True, 'SPIDER_MODULES': ['cartrider.spiders']}
2019-12-05 15:32:48 [scrapy.extensions.telnet] INFO: Telnet Password: d2dd210eb970958a
2019-12-05 15:32:48 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.feedexport.FeedExporter',
 'scrapy.exten

2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0081000c49de66ce HTTP/1.1" 200 2351
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/01e4001049dd0903 HTTP/1.1" 200 817
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/02a9001049dcf740 HTTP/1.1" 200 890
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:50 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0213001049dcf2cb HTTP/1.1" 200 886
2019-12-05 15:3

2019-12-05 15:32:52 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/009b001049dc9a99 HTTP/1.1" 200 2352
2019-12-05 15:32:52 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:52 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0284001049dc9605 HTTP/1.1" 200 887
2019-12-05 15:32:52 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:52 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0108000e49dc03c8 HTTP/1.1" 200 1694
2019-12-05 15:32:52 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:53 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/02d7000c49ddf046 HTTP/1.1" 200 1290
2019-12-05 15:32:53 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15

2019-12-05 15:32:55 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/00f9001049dd0ad8 HTTP/1.1" 200 881
2019-12-05 15:32:55 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:55 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0081000c49de66ce HTTP/1.1" 200 2351
2019-12-05 15:32:55 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:56 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/01e4001049dd0903 HTTP/1.1" 200 817
2019-12-05 15:32:56 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:56 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/02a9001049dcf740 HTTP/1.1" 200 890
2019-12-05 15:32:56 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:3

2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/02a9001049dcf740 HTTP/1.1" 200 890
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0213001049dcf2cb HTTP/1.1" 200 886
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0036001049dcf4ee HTTP/1.1" 200 822
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/02bd001049dcf099 HTTP/1.1" 200 884
2019-12-05 15:32:59 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:32

...

2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0272000e49ede442 HTTP/1.1" 200 881
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0258000e49ede432 HTTP/1.1" 200 1343
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/01c0001049ee7a0a HTTP/1.1" 200 824
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:38 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/012d000c49efd573 HTTP/1.1" 200 3162
2019-12-05 15:

2019-12-05 15:53:41 [scrapy.core.scraper] DEBUG: Scraped from <200 https://api.nexon.co.kr/kart/v1.0/matches/00a9000c49f01d59>
{'kart': 'ffd2a1758730357726de85bdcf68789e4c38980fcebc62e25b9e71aabf6e732f',
 'matchRank': '7',
 'matches': '00a9000c49f01d59',
 'rankinggrade2': '3',
 'trackId': ''}
2019-12-05 15:53:41 [scrapy.core.scraper] DEBUG: Scraped from <200 https://api.nexon.co.kr/kart/v1.0/matches/00a9000c49f01d59>
{'kart': '',
 'matchRank': '1',
 'matches': '00a9000c49f01d59',
 'rankinggrade2': '5',
 'trackId': ''}
2019-12-05 15:53:41 [scrapy.core.scraper] DEBUG: Scraped from <200 https://api.nexon.co.kr/kart/v1.0/matches/00a9000c49f01d59>
{'kart': '09da315c5777b7cd193f07f3f0797595fdc360498a2f6544e569e64008a98a86',
 'matchRank': '5',
 'matches': '00a9000c49f01d59',
 'rankinggrade2': '0',
 'trackId': ''}
2019-12-05 15:53:41 [scrapy.core.scraper] DEBUG: Scraped from <200 https://api.nexon.co.kr/kart/v1.0/matches/00a9000c49f01d59>
{'kart': '9bc087c44de7d959774ab7bc1a624539b805b535f5512

2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/7ac9001049ee4f31 HTTP/1.1" 200 892
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/03f1000c49efaac9 HTTP/1.1" 200 1349
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/03c7000c49efa962 HTTP/1.1" 200 2337
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0282001049ee49e2 HTTP/1.1" 200 1894
2019-12-05 15:53:43 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15

2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/008f000e49eda0ff HTTP/1.1" 200 1768
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/002a000c49ef91a4 HTTP/1.1" 200 1956
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0392001049ee31d5 HTTP/1.1" 200 887
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/020f001049ee3158 HTTP/1.1" 200 1875
2019-12-05 15:53:45 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15

2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0156000e49ed8970 HTTP/1.1" 200 4002
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0030000e49ed8b16 HTTP/1.1" 200 887
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/036c000e49ed88f3 HTTP/1.1" 200 2276
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: https://api.nexon.co.kr:443 "GET /kart/v1.0/matches/0017000e49ed8549 HTTP/1.1" 200 1365
2019-12-05 15:53:47 [urllib3.connectionpool] DEBUG: Starting new HTTPS connection (1): api.nexon.co.kr:443
2019-12-05 15